In [0]:
# pyspark functions
from pyspark.sql.functions import *
# URL processing
import urllib

In [0]:
# Define the path to the Delta table
delta_table_path = "dbfs:/user/hive/warehouse/authentication_credentials"

# Read the Delta table to a Spark DataFrame
aws_keys_df = spark.read.format("delta").load(delta_table_path)

In [0]:
# Get the AWS access key and secret key from the spark dataframe
ACCESS_KEY = aws_keys_df.select('Access key ID').collect()[0]['Access key ID']
SECRET_KEY = aws_keys_df.select('Secret access key').collect()[0]['Secret access key']
# Encode the secrete key
ENCODED_SECRET_KEY = urllib.parse.quote(string=SECRET_KEY, safe="")

In [0]:
# AWS S3 bucket name
AWS_S3_BUCKET = "user-0affdc2332e7-bucket"

MOUNT_NAME = "/mnt/0affdc2332e7_mount"

# Source url
SOURCE_URL = "s3n://{0}:{1}@{2}".format(ACCESS_KEY, ENCODED_SECRET_KEY, AWS_S3_BUCKET)
# Mount the drive
dbutils.fs.mount(SOURCE_URL, MOUNT_NAME)

--------------------------------------------------------------------------- 
 ExecutionError Traceback (most recent call last)
 <command-764650334901328> in <module> 
 7 SOURCE_URL = "s3n://{0}:{1}@{2}" . format ( ACCESS_KEY , ENCODED_SECRET_KEY , AWS_S3_BUCKET ) 
 8 # Mount the drive 
 ----> 9 dbutils . fs . mount ( SOURCE_URL , MOUNT_NAME ) 

 /databricks/python_shell/dbruntime/dbutils.py in f_with_exception_handling (*args, **kwargs) 
 387 exc . __context__ = None 
 388 exc . __cause__ = None 
 --> 389 raise exc
 390 
 391 return f_with_exception_handling

 ExecutionError : An error occurred while calling o572.mount.
: java.rmi.RemoteException: java.lang.IllegalArgumentException: requirement failed: Directory already mounted: /mnt/0affdc2332e7_mount; nested exception is: 
	java.lang.IllegalArgumentException: requirement failed: Directory already mounted: /mnt/0affdc2332e7_mount
	at com.databricks.backend.daemon.data.client.DbfsClient.send0(DbfsClient.scala:128)
	at com.databricks.backend.daemon.data.client.DbfsClient.sendIdempotent(DbfsClient.scala:68)
	at com.databricks.backend.daemon.dbutils.DBUtilsCore.createOrUpdateMount(DBUtilsCore.scala:756)
	at com.databricks.backend.daemon.dbutils.DBUtilsCore.mount(DBUtilsCore.scala:776)
	at sun.reflect.NativeMethodAccessorImpl.invoke0(Native Method)
	at sun.reflect.NativeMethodAccessorImpl.invoke(NativeMethodAccessorImpl.java:62)
	at sun.reflect.DelegatingMethodAccessorImpl.invoke(DelegatingMethodAccessorImpl.java:43)
	at java.lang.reflect.Method.invoke(Method.java:498)
	at py4j.reflection.MethodInvoker.invoke(MethodInvoker.java:244)
	at py4j.reflection.ReflectionEngine.invoke(ReflectionEngine.java:380)
	at py4j.Gateway.invoke(Gateway.java:295)
	at py4j.commands.AbstractCommand.invokeMethod(AbstractCommand.java:132)
	at py4j.commands.CallCommand.execute(CallCommand.java:79)
	at py4j.GatewayConnection.run(GatewayConnection.java:251)
	at java.lang.Thread.run(Thread.java:750)
Caused by: java.lang.IllegalArgumentException: requirement failed: Directory already mounted: /mnt/0affdc2332e7_mount
	at scala.Predef$.require(Predef.scala:281)
	at com.databricks.backend.daemon.data.server.DefaultMetadataManager.$anonfun$insertMount$1(MetadataManager.scala:703)
	at com.databricks.backend.daemon.data.server.DefaultMetadataManager.$anonfun$modifyAndVerify$2(MetadataManager.scala:1085)
	at scala.runtime.java8.JFunction0$mcV$sp.apply(JFunction0$mcV$sp.java:23)
	at com.databricks.backend.daemon.data.server.DefaultMetadataManager.withRetries(MetadataManager.scala:858)
	at com.databricks.backend.daemon.data.server.DefaultMetadataManager.modifyAndVerify(MetadataManager.scala:1074)
	at com.databricks.backend.daemon.data.server.DefaultMetadataManager.insertMount(MetadataManager.scala:711)
	at com.databricks.backend.daemon.data.server.handler.MountHandler.receive(MountHandler.scala:128)
	at com.databricks.backend.daemon.data.server.session.SessionContext.$anonfun$queryHandlers$1(SessionContext.scala:54)
	at com.databricks.backend.daemon.data.server.session.SessionContext.$anonfun$queryHandlers$1$adapted(SessionContext.scala:53)
	at scala.collection.immutable.List.foreach(List.scala:431)
	at com.databricks.backend.daemon.data.server.session.SessionContext.queryHandlers(SessionContext.scala:53)
	at com.databricks.backend.daemon.data.server.DbfsServerBackend$$anonfun$receive$4.$anonfun$applyOrElse$10(DbfsServerBackend.scala:472)
	at com.databricks.logging.AttributionContextTracing.$anonfun$withAttributionContext$1(AttributionContextTracing.scala:48)
	at com.databricks.logging.AttributionContext$.$anonfun$withValue$1(AttributionContext.scala:275)
	at scala.util.DynamicVariable.withValue(DynamicVariable.scala:62)
	at com.databricks.logging.AttributionContext$.withValue(AttributionContext.scala:271)
	at com.databricks.logging.AttributionContextTracing.withAttributionContext(AttributionContextTracing.scala:46)
	at com.databricks.logging.AttributionContextTracing.withAttributionContext$(AttributionContextTracing.

In [0]:
%sql
-- Disable format checks during the reading of Delta tables
SET spark.databricks.delta.formatCheck.enabled=false

key value spark.databricks.delta.formatCheck.enabled false

In [0]:
# Define file locations and types for each topic
file_type = "json"
infer_schema = "true"

pin_file_location = "/mnt/0affdc2332e7_mount/topics/0affdc2332e7.pin/partition=0/*.json"
user_file_location = "/mnt/0affdc2332e7_mount/topics/0affdc2332e7.user/partition=0/*.json"
geo_file_location = "/mnt/0affdc2332e7_mount/topics/0affdc2332e7.geo/partition=0/*.json"

# Read in JSONs from mounted S3 bucket for each topic
df_pin = spark.read.format(file_type) \
    .option("inferSchema", infer_schema) \
    .load(pin_file_location)

df_user = spark.read.format(file_type) \
    .option("inferSchema", infer_schema) \
    .load(user_file_location)

df_geo = spark.read.format(file_type) \
    .option("inferSchema", infer_schema) \
    .load(geo_file_location)

# Display Spark DataFrames to check their contents
display(df_pin)
# display(df_user)
# display(df_geo)


category description downloaded follower_count image_src index is_image_or_video poster_name save_location tag_list title unique_id mens-fashion スポーツミックススタイルやアスレジャースタイルの台頭によって、すっかりおなじみとなった「ジョガーパンツ」。スニーカーと相性抜群なアイテムであり、フーディを合わせたカジュアルなスタイルからジャケットを羽織ったドレスライクなスタイルまで幅広くフィットする。今回はそんな「ジョガーパンツ」にフォーカスして注目の着こなし&アイテムを紹介！ 1 122k https://i.pinimg.com/originals/5d/31/e4/5d31e49fada653798f7c8f4c47f65d14.jpg 7491 image OTOKOMAE/男前研究所 Local save in /data/mens-fashion Streetwear,Mens Casual Hats,Fashion Week Hommes,Herren Style,Moda Blog,Look Man,La Mode Masculine,Outfits With Converse,Black Converse ジョガーパンツでメンズコーデの足元を軽快にこなす！ | メンズファッションメディア OTOKOMAE 0bfd8ee2-8bc8-4d43-8a43-3f9e5f9678bf vehicles !Закрыто! Хотите эстетику или кое-какие элементы для фанфиков? Если это так, то вам, определённо, стоит заглянуть сюда. 𝐅𝐚𝐧𝐜𝐢 𝐅 𝐨𝐫 𝐱𝐱𝐬𝐚𝐣𝐧𝐱 1 422 https://i.pinimg.com/originals/ed/45/25/ed452567d0affd9329d33cc6fb14b5d6.jpg 11100 image Tia Local save in /data/vehicles Cool Sports Cars,Sport Cars,Cool Cars,Top Luxury Cars,Lamborghini Cars,Lamborghini Urus Interior,Lux Cars,Street Racing Cars,Pretty Cars 𝒜𝑒𝓈𝓉𝒽𝑒𝓉𝒾𝒸 / 𝒻𝑜𝓇 𝒻𝒶𝓃𝒻𝒾𝒸𝓈 c5474c35-4711-416b-b627-764d51498916 tattoos Elmira Kruger shared a photo on Instagram: “Больше всего жалко девчонок, которые экономят и разукрашивают свои красивые тела ляпистыми не…” • See 1,214 photos and videos on thei…  1 848 https://i.pinimg.com/originals/9e/4e/a8/9e4ea85a446f779c6d0a1fdc785e9d4b.jpg 8822 image Alicia Keller Local save in /data/tattoos Arm Sleeve Tattoos For Women,Chicano Tattoos Sleeve,Full Sleeve Tattoos,Body Art Tattoos,Girl Tattoos,Arabic Tattoos,Badass Sleeve Tattoos,Portrait Tattoo Sleeve,Tattoos Pics Elmira Kruger on Instagram: “Больше всего жалко девчонок, которые экономят и разукрашивают свои красивые тела ляпистыми не стильными рисунками☹️ Я в женском рукаве…” db80a4e4-293a-45cf-b60c-a67ba9053246 home-decor Вместе с Русланом Кирничанским рассказываем, как выжать максимум из маленькой площади и продумать системы хранения так, чтобы ими было удобно пользоваться. Свежие идеи дизайна и…  1 35k https://i.pinimg.com/originals/0b/5c/0f/0b5c0fdd3ea40beff4a91ddcdaf98852.jpg 5996 image INMYROOM.RU Local save in /data/home-decor Scandinavian Interior Design,Home Interior Design,Scandinavian Style,Swedish Decor,Swedish Style,Interior Door,Interior Modern,Minimalist Interior,Scandi Chic Где найти и как организовать дополнительные места для хранения? — INMYROOM 4081ef06-637d-4cfb-9195-5e06b56fbd8c event-planning Το όνομα που επέλεξε η μαμά Ανδριανή για τη γλυκιά Τιτίκα δεν είναι καθόλου τυχαίο. Και φυσικά δεν άφησε τίποτα στην τύχη ούτε την ημέρα της βάπτισης. Ανέθεσε την οργάνωση στην…  1 4 https://i.pinimg.com/originals/db/aa/d2/dbaad28fa85012a4ea6958540d98a8e5.jpg 4387 image Manosbojana Katsareas Local save in /data/event-planning Diy Flowers,Flower Diy,Baptism Decorations,Christening,Event Planning,Wedding Planner,Baptism Ideas,Birthday,Party Βάπτιση: H παραμυθένια βάπτιση της Τιτίκας με θέμα το μονόκερο από την e.m. for you ae5e7377-f1bd-4ac5-94de-bee317f51a43 home-decor Так повелось в последнее время, что по субботам мы делимся фотографиями какой-нибудь милой скандинавской дачи (надеюсь никто не против такой нашей ✌PUFIK. Beautiful Interiors. O…  1 136k https://i.pinimg.com/originals/25/82/6b/25826bbe3789faa1c1c70d78ad93a33c.jpg 5953 image PUFIK Interiors & Inspirations Local save in /data/home-decor Cottage Living Rooms,Cottage Interiors,Home Living Room,Cottage Style Living Room,Cottage House,Cozy Living,Cottage Style Decor,Country Decor,Country Cottage Decorating 〚 Vintage summer cottage filled with love and charm in Sweden 〛◾ Photos ◾ Ideas ◾ Design 0c15cec8-5e8d-42e7-a2ad-9bd1267e0679 diy-and-crafts Make this adorable (and easy) DIY doll crib from an old cardboard box, your little one will love to rock their dolls to sleep in this fun upcycled project! 1 66k https://i.pinimg.com/originals/62/ee/0d/62ee0d79f92248b2d5819b8bfdd94551.jpg 3020 image Cassie May - Little Red Window Crafts, DIY, crafts, tutorials

In [0]:
# Define the output locations for Parquet files
pin_parquet_location = "/mnt/0affdc2332e7_mount/combined_data_objects_parquet/pin"
user_parquet_location = "/mnt/0affdc2332e7_mount/combined_data_objects_parquet/user"
geo_parquet_location = "/mnt/0affdc2332e7_mount/combined_data_objects_parquet/geo"

# Write DataFrames as Parquet files
df_pin.write.parquet(pin_parquet_location)
df_user.write.parquet(user_parquet_location)
df_geo.write.parquet(geo_parquet_location)

--------------------------------------------------------------------------- 
 AnalysisException Traceback (most recent call last)
 <command-4496652113491171> in <module> 
 5 
 6 # Write DataFrames as Parquet files 
 ----> 7 df_pin . write . parquet ( pin_parquet_location ) 
 8 df_user . write . parquet ( user_parquet_location ) 
 9 df_geo . write . parquet ( geo_parquet_location ) 

 /databricks/spark/python/pyspark/sql/readwriter.py in parquet (self, path, mode, partitionBy, compression) 
 883 self . partitionBy ( partitionBy ) 
 884 self . _set_opts ( compression = compression ) 
 --> 885 self . _jwrite . parquet ( path ) 
 886 
 887 def text ( self , path , compression = None , lineSep = None ) : 

 /databricks/spark/python/lib/py4j-0.10.9.1-src.zip/py4j/java_gateway.py in __call__ (self, *args) 
 1302 
 1303 answer = self . gateway_client . send_command ( command ) 
 -> 1304 return_value = get_return_value(
 1305 answer, self.gateway_client, self.target_id, self.name)
 1306 

 /databricks/spark/python/pyspark/sql/utils.py in deco (*a, **kw) 
 121 # Hide where the exception came from that shows a non-Pythonic 
 122 # JVM exception message. 
 --> 123 raise converted from None 
 124 else : 
 125 raise 

 AnalysisException : path dbfs:/mnt/0affdc2332e7_mount/combined_data_objects_parquet/pin already exists.

In [0]:
df_pin_parquet = spark.read.parquet(pin_parquet_location)
df_geo_parquet = spark.read.parquet(geo_parquet_location)
df_user_parquet = spark.read.parquet(user_parquet_location)

In [0]:
display(df_pin_parquet)

category description downloaded follower_count image_src index is_image_or_video poster_name save_location tag_list title unique_id mens-fashion スポーツミックススタイルやアスレジャースタイルの台頭によって、すっかりおなじみとなった「ジョガーパンツ」。スニーカーと相性抜群なアイテムであり、フーディを合わせたカジュアルなスタイルからジャケットを羽織ったドレスライクなスタイルまで幅広くフィットする。今回はそんな「ジョガーパンツ」にフォーカスして注目の着こなし&アイテムを紹介！ 1 122k https://i.pinimg.com/originals/5d/31/e4/5d31e49fada653798f7c8f4c47f65d14.jpg 7491 image OTOKOMAE/男前研究所 Local save in /data/mens-fashion Streetwear,Mens Casual Hats,Fashion Week Hommes,Herren Style,Moda Blog,Look Man,La Mode Masculine,Outfits With Converse,Black Converse ジョガーパンツでメンズコーデの足元を軽快にこなす！ | メンズファッションメディア OTOKOMAE 0bfd8ee2-8bc8-4d43-8a43-3f9e5f9678bf vehicles !Закрыто! Хотите эстетику или кое-какие элементы для фанфиков? Если это так, то вам, определённо, стоит заглянуть сюда. 𝐅𝐚𝐧𝐜𝐢 𝐅 𝐨𝐫 𝐱𝐱𝐬𝐚𝐣𝐧𝐱 1 422 https://i.pinimg.com/originals/ed/45/25/ed452567d0affd9329d33cc6fb14b5d6.jpg 11100 image Tia Local save in /data/vehicles Cool Sports Cars,Sport Cars,Cool Cars,Top Luxury Cars,Lamborghini Cars,Lamborghini Urus Interior,Lux Cars,Street Racing Cars,Pretty Cars 𝒜𝑒𝓈𝓉𝒽𝑒𝓉𝒾𝒸 / 𝒻𝑜𝓇 𝒻𝒶𝓃𝒻𝒾𝒸𝓈 c5474c35-4711-416b-b627-764d51498916 tattoos Elmira Kruger shared a photo on Instagram: “Больше всего жалко девчонок, которые экономят и разукрашивают свои красивые тела ляпистыми не…” • See 1,214 photos and videos on thei…  1 848 https://i.pinimg.com/originals/9e/4e/a8/9e4ea85a446f779c6d0a1fdc785e9d4b.jpg 8822 image Alicia Keller Local save in /data/tattoos Arm Sleeve Tattoos For Women,Chicano Tattoos Sleeve,Full Sleeve Tattoos,Body Art Tattoos,Girl Tattoos,Arabic Tattoos,Badass Sleeve Tattoos,Portrait Tattoo Sleeve,Tattoos Pics Elmira Kruger on Instagram: “Больше всего жалко девчонок, которые экономят и разукрашивают свои красивые тела ляпистыми не стильными рисунками☹️ Я в женском рукаве…” db80a4e4-293a-45cf-b60c-a67ba9053246 home-decor Вместе с Русланом Кирничанским рассказываем, как выжать максимум из маленькой площади и продумать системы хранения так, чтобы ими было удобно пользоваться. Свежие идеи дизайна и…  1 35k https://i.pinimg.com/originals/0b/5c/0f/0b5c0fdd3ea40beff4a91ddcdaf98852.jpg 5996 image INMYROOM.RU Local save in /data/home-decor Scandinavian Interior Design,Home Interior Design,Scandinavian Style,Swedish Decor,Swedish Style,Interior Door,Interior Modern,Minimalist Interior,Scandi Chic Где найти и как организовать дополнительные места для хранения? — INMYROOM 4081ef06-637d-4cfb-9195-5e06b56fbd8c event-planning Το όνομα που επέλεξε η μαμά Ανδριανή για τη γλυκιά Τιτίκα δεν είναι καθόλου τυχαίο. Και φυσικά δεν άφησε τίποτα στην τύχη ούτε την ημέρα της βάπτισης. Ανέθεσε την οργάνωση στην…  1 4 https://i.pinimg.com/originals/db/aa/d2/dbaad28fa85012a4ea6958540d98a8e5.jpg 4387 image Manosbojana Katsareas Local save in /data/event-planning Diy Flowers,Flower Diy,Baptism Decorations,Christening,Event Planning,Wedding Planner,Baptism Ideas,Birthday,Party Βάπτιση: H παραμυθένια βάπτιση της Τιτίκας με θέμα το μονόκερο από την e.m. for you ae5e7377-f1bd-4ac5-94de-bee317f51a43 home-decor Так повелось в последнее время, что по субботам мы делимся фотографиями какой-нибудь милой скандинавской дачи (надеюсь никто не против такой нашей ✌PUFIK. Beautiful Interiors. O…  1 136k https://i.pinimg.com/originals/25/82/6b/25826bbe3789faa1c1c70d78ad93a33c.jpg 5953 image PUFIK Interiors & Inspirations Local save in /data/home-decor Cottage Living Rooms,Cottage Interiors,Home Living Room,Cottage Style Living Room,Cottage House,Cozy Living,Cottage Style Decor,Country Decor,Country Cottage Decorating 〚 Vintage summer cottage filled with love and charm in Sweden 〛◾ Photos ◾ Ideas ◾ Design 0c15cec8-5e8d-42e7-a2ad-9bd1267e0679 diy-and-crafts Make this adorable (and easy) DIY doll crib from an old cardboard box, your little one will love to rock their dolls to sleep in this fun upcycled project! 1 66k https://i.pinimg.com/originals/62/ee/0d/62ee0d79f92248b2d5819b8bfdd94551.jpg 3020 image Cassie May - Little Red Window Crafts, DIY, crafts, tutorials

In [0]:
# Finding null values

cols = df_pin_parquet.columns

# Create list of conditions for each column
conditions = [col(c).isNull() | (col(c) == "") for c in cols]

# Combine conditions using logical OR (|)
combined_condition = conditions[0]
for condition in conditions[1:]:
    combined_condition = combined_condition | condition

# Apply the filter
df_filtered = df_pin_parquet.filter(combined_condition)

display(df_filtered)

category description downloaded follower_count image_src index is_image_or_video poster_name save_location tag_list title unique_id event-planning Elegant rose and hydrangeas mirror box are great to have for a centerpiece or any type of elegant event that you may have.Materials Square styrofoam block 7.... 0 717 null 4467 null Aleksandra Kitajewska Local save in /data/event-planning Birthday Centerpieces,Diy Centerpieces,Diy Wedding Decorations,Centerpiece Wedding,Centerpieces With Mirrors,Wedding Ideas,Glam Mirror,Mirror Box,Mirror Centerpiece DIY| BLING GLAM MIRROR CENTERPIECE / WEDDINGS COLLECTION 2017 44ae2976-49c6-4cbe-83b9-ecc8ab3f0b24 event-planning Many Event Planners start out working from home. This can be a great model for setting up an event planning business as it keeps overheads down in those critical early stages of…  0 9k null 4760 null EventMB Local save in /data/event-planning Wedding Reception Planning,Wedding Event Planner,Wedding Events,Budget Wedding,Wedding Ideas,Tent Wedding,Weddings,Event Planning Tips,Event Planning Business How to Start an Event Planning Business from Home (2020 Edition) 49cab875-8a35-4dc2-9811-82b1440e5aa8 event-planning A golf themed party can be perfect for a myriad of events like showers, engagements, retirement, rehearsal dinners and even a high school golf team banquet. That's were my first…  0 536 null 4770 null Paula Samples Local save in /data/event-planning Golf Table Decorations,Banquet Centerpieces,Retirement Party Decorations,Retirement Parties,Golf Party Favors,Golf Wedding,Golf Theme,Party Themes,Party Ideas How to Make a Centerpiece for a Golf Themed Party bcf7899a-0862-4a3d-807e-dfc6b650f36d event-planning Pricing your event planning service is an important thing to figure out as an event planner. This video discusses the 5 main ways you can charge:1. Hourly ra... 0 224 null 4521 null Ka Welch Local save in /data/event-planning Event Planning Tips,Event Planning Business,Party Planning,Wedding Planning,Wedding Ideas,Budget Wedding,Becoming An Event Planner,Business Pictures,Personal Finance How to Charge for Your Event Planning Services 953f5cfa-0886-4652-bd1c-5977198acb59 event-planning How to START an event planning business in 2020, I'm sharing 5 tips to help you get started. Whether you're a wedding planner or corporate events planner loo... 0 3 null 4727 null KaY 864-735-4058 Local save in /data/event-planning Event Planning Tips,Event Planning Business,Party Planning,Corporate Event Planner,Corporate Events,Event Planners,Tent Wedding,Wedding Events,Weddings 5 TIPS FOR STARTING AN EVENT PLANNING BUSINESS IN 2020 6d43e998-468f-4098-8f5b-5556e1e02476 event-planning Building your event planning portfolio is an important thing to do so you can get more clients in the future. This video discusses the 8 main ways you can bu... 0 258 null 4540 null Ajahna Blaze Local save in /data/event-planning Event Planning Business,Event Management,How To Plan,Budget,Building,Party Planning,Wedding Planning,Aisle Decorations,Church Events How to Build Your Event Planning Portfolio 244fad8e-006d-4760-a023-20bfc4a047b2 art Since my childhood I always loved bubbles and water drops. For some reason, I find beauty in them. So as 0 96k null 360 null Acrylic Pouring Local save in /data/art Acrylic Pouring Techniques,Acrylic Pouring Art,Acrylic Art,Painting Techniques,Acrylic Paintings,Tree Paintings,Easy Paintings,Acrylic Nails,Water Droplets How to Add 3D Water Droplets in Your Acrylic Pour 5cd07006-0284-4860-9c64-03908c39f43b finance No description available Story format 0 57k Image src error. 5658 multi-video(story page format) GenTwenty | Personal Growth, Self-Care, and Money Local save in /data/finance Ways To Save Money,Money Tips,Money Saving Tips,Money Hacks,Saving Ideas,Budgeting Finances,Budgeting Tips,Planning Budget,Money Saving Challenge 742e2019-6a68-44ad-a143-1b90e1fa4afa finance No description available Story format 0 98k Image src error. 5718 multi-video(story page forma

In [0]:
# Replace irrelevant entries and empty entries with None 

# Dictionary mapping column names to their irrelevant text or empty string values
irrelevant_entries = {
    "title": ["", "No Title Data Available"],
    "description": "No description available Story format",
    "image_src": "Image src error.",
    "tag_list": "N,o, ,T,a,g,s, ,A,v,a,i,l,a,b,l,e",
    "poster_name": "User Info Error",
    "follower_count": "User Info Error"
}

for col_name, entries in irrelevant_entries.items():
    df_pin_parquet = df_pin_parquet.withColumn(col_name, when(col(col_name).isin(entries), None).otherwise(col(col_name)))



In [0]:
# Converting entries in the follower_count column to numbers and changing the data type to int

df_pin_parquet = df_pin_parquet.withColumn(
    "follower_count", 
    when(col("follower_count").endswith("k"), regexp_replace(col("follower_count"), "k", "").cast("int") * 1000)
    .when(col("follower_count").endswith("M"), regexp_replace(col("follower_count"), "M", "").cast("int") * 1000000)
    .otherwise(col("follower_count").cast("int"))
)

In [0]:
# Cleaning the data in the save_location column to only include the path to the data

df_pin_parquet = df_pin_parquet.withColumn(
    "save_location", 
    when(col("save_location").startswith("Local save in "), regexp_replace(col("save_location"), "Local save in ", "")).otherwise(col("save_location"))
)

In [0]:
# Rename index column to ind

df_pin_parquet = df_pin_parquet.withColumnRenamed("index", "ind")

In [0]:
# Reordering the columns 

df_pin_parquet = df_pin_parquet.select("ind", "unique_id", "title", "description", "follower_count", "poster_name", "tag_list", "is_image_or_video", "image_src", "save_location", "category")

In [0]:
# Dropping duplicates

df_pin_parquet = df_pin_parquet.dropDuplicates()

In [0]:
# Cleaning geo data

# Creating new coordinates column which is an array of latitude and longitude columns

df_geo_parquet = df_geo_parquet.withColumn("coordinates", concat("latitude", lit(", "), "longitude"))

In [0]:
# Dropping latitude and longitude columns

df_geo_parquet = df_geo_parquet.drop("latitude", "longitude")

In [0]:
# Converting timestamp column to timestamp 

df_geo_parquet = df_geo_parquet.withColumn("new_timestamp", to_timestamp("timestamp", "yyyy-MM-dd HH:mm:ss"))

In [0]:
# Reordering columns 

df_geo_parquet = df_geo_parquet.withColumnRenamed("index", "ind")

df_geo_parquet = df_geo_parquet.select("ind", "country", "coordinates", "new_timestamp")

In [0]:
# Dropping null values

df_geo_parquet = df_geo_parquet.dropna()

In [0]:
# Dropping duplicates

df_geo_parquet = df_geo_parquet.dropDuplicates()

In [0]:
# Cleaning user data

# Creating new column for user's full name

df_user_parquet = df_user_parquet.withColumn("user_name", concat("first_name", lit(" "), "last_name"))

In [0]:
# Dropping the first_name and last_name columns

df_user_parquet = df_user_parquet.drop("first_name", "last_name")

In [0]:
# Converting date_joined to timestamp 

df_user_parquet = df_user_parquet.withColumn("date_joined", to_timestamp("date_joined"))

In [0]:
# Renaming index column and reordering columns

df_user_parquet = df_user_parquet.withColumnRenamed("index", "ind")

df_user_parquet = df_user_parquet.select("ind", "user_name", "age", "date_joined")

In [0]:
# Dropping duplicates

df_user_parquet = df_user_parquet.dropDuplicates()

In [0]:
# Find the most popular Pinterest category people post to based on their country.

joined_df = df_geo_parquet.join(df_pin_parquet, on="ind", how="inner")

most_popular_category = joined_df.groupBy("country", "category") \
                                 .agg(count("*").alias("Count")) \
                                 .orderBy("country", desc("Count")) 

most_popular_cat_by_country = most_popular_category.groupBy("country") \
                                                   .agg(
                                                            first("category").alias("MostPopularCategory"),
                                                            max("Count").alias("TotalCount")
                                                        ).orderBy("country")  
                                                   
display(most_popular_cat_by_country)


country MostPopularCategory TotalCount Afghanistan education 94 Albania art 193 Algeria quotes 256 American Samoa tattoos 98 Andorra tattoos 77 Angola education 30 Anguilla christmas 25 Antarctica (the territory South of 60 deg S) christmas 36 Antigua and Barbuda travel 29 Argentina tattoos 72 Armenia vehicles 28 Aruba christmas 56 Australia christmas 17 Austria tattoos 30 Azerbaijan finance 35 Bahamas event-planning 41 Bahrain finance 12 Bangladesh christmas 36 Barbados art 24 Belarus travel 19 Belgium diy-and-crafts 14 Belize diy-and-crafts 22 Benin tattoos 20 Bermuda tattoos 22 Bhutan event-planning 10 Bolivia home-decor 27 Bosnia and Herzegovina tattoos 23 Botswana finance 17 Bouvet Island (Bouvetoya) travel 26 Brazil home-decor 15 British Indian Ocean Territory (Chagos Archipelago) mens-fashion 15 British Virgin Islands christmas 20 Brunei Darussalam event-planning 9 Bulgaria education 17 Burkina Faso vehicles 14 Burundi beauty 13 Cambodia beauty 8 Cameroon art 13 Canada event-planning 10 Cape Verde travel 11 Cayman Islands diy-and-crafts 8 Central African Republic education 12 Chad diy-and-crafts 16 Chile mens-fashion 11 China vehicles 5 Christmas Island travel 18 Cocos (Keeling) Islands finance 9 Colombia christmas 12 Comoros diy-and-crafts 15 Congo travel 17 Cook Islands diy-and-crafts 9 Costa Rica home-decor 16 Cote d'Ivoire beauty 10 Croatia finance 11 Cuba tattoos 11 Cyprus vehicles 13 Czech Republic travel 12 Denmark education 9 Djibouti diy-and-crafts 8 Dominica finance 4 Dominican Republic education 12 Ecuador travel 14 Egypt vehicles 14 El Salvador travel 7 Equatorial Guinea quotes 5 Eritrea christmas 5 Estonia christmas 10 Ethiopia art 10 Falkland Islands (Malvinas) christmas 10 Faroe Islands event-planning 9 Fiji education 7 Finland finance 8 France beauty 7 French Guiana finance 7 French Polynesia event-planning 14 French Southern Territories quotes 4 Gabon diy-and-crafts 6 Gambia diy-and-crafts 6 Georgia education 8 Germany event-planning 12 Ghana beauty 4 Gibraltar mens-fashion 5 Greece mens-fashion 10 Greenland vehicles 6 Grenada quotes 12 Guadeloupe christmas 9 Guam quotes 5 Guatemala diy-and-crafts 7 Guernsey tattoos 5 Guinea finance 5 Guinea-Bissau travel 8 Guyana vehicles 5 Haiti christmas 8 Heard Island and McDonald Islands vehicles 9 Holy See (Vatican City State) tattoos 5 Honduras event-planning 6 Hong Kong education 4 Hungary vehicles 6 Iceland beauty 4 India art 8 Indonesia finance 8 Iran christmas 5 Iraq christmas 9 Ireland mens-fashion 4 Isle of Man art 6 Israel education 7 Italy vehicles 8 Jamaica education 9 Japan art 6 Jersey quotes 5 Jordan home-decor 5 Kazakhstan christmas 7 Kenya mens-fashion 7 Kiribati christmas 5 Korea art 9 Kuwait travel 11 Kyrgyz Republic christmas 8 Lao People's Democratic Republic beauty 6 Latvia travel 5 Lebanon vehicles 8 Lesotho art 6 Liberia travel 4 Libyan Arab Jamahiriya vehicles 5 Liechtenstein diy-and-crafts 6 Lithuania diy-and-crafts 3 Luxembourg event-planning 3 Macao vehicles 9 Macedonia vehicles 4 Madagascar mens-fashion 7 Malawi mens-fashion 6 Malaysia diy-and-crafts 4 Maldives event-planning 4 Mali christmas 5 Malta event-planning 6 Marshall Islands event-planning 5 Martinique art 6 Mauritania christmas 4 Mauritius home-decor 3 Mayotte education 4 Mexico home-decor 4 Micronesia event-planning 4 Moldova beauty 6 Monaco mens-fashion 5 Mongolia travel 5 Montenegro mens-fashion 4 Montserrat vehicles 8 Morocco education 5 Mozambique home-decor 5 Myanmar christmas 8 Namibia vehicles 5 Nauru mens-fashion 6 Nepal christmas 5 Netherlands home-decor 6 Netherlands Antilles art 7 New Caledonia beauty 4 New Zealand mens-fashion 4 Nicaragua vehicles 5 Niger beauty 5 Nigeria mens-fashion 7 Niue tattoos 4 Norfolk Island beauty 5 Northern Mariana Islands education 2 Norway vehicles 3 Oman finance 5 Pakistan education 3 Palau vehicles 4 Palestinian Territory christmas 7 Panama vehicles 5 Papua New Guinea travel 6 Paraguay vehicles 5 Peru beauty 4 Philippines mens-fashion

In [0]:
# Find the most popular category each year

df_geo_parquet_with_year = df_geo_parquet.withColumn("year", year(col("new_timestamp")))

joined_df_with_year = df_geo_parquet_with_year.join(df_pin_parquet, on="ind", how="inner")

most_popular_cat = joined_df_with_year.groupBy("year", "category") \
                                            .agg(count("*").alias("Count")) \
                                            .orderBy("year", desc("Count")) 

most_popular_cat_by_year = most_popular_cat.groupBy("year") \
                                                   .agg(
                                                        first("category").alias("MostPopularCategory"),
                                                        max("Count").alias("TotalCount")
                                                    ).orderBy("year") 
                                                   
display(most_popular_cat_by_year)


year MostPopularCategory TotalCount 2017 home-decor 42 2018 christmas 210 2019 christmas 205 2020 christmas 191 2021 education 200 2022 christmas 171

In [0]:
# Find the users with the most followers in each country

from pyspark.sql.window import Window

followers_by_country = joined_df.groupBy("poster_name", "country") \
                            .agg(max("follower_count").alias("followers")) \
                            .orderBy("country", desc("followers"))

window_spec = Window.partitionBy("country").orderBy(col("followers").desc())

ranked_followers_by_country = followers_by_country.withColumn("rank", row_number().over(window_spec))

top_poster_per_country = ranked_followers_by_country.filter(col("rank") == 1).drop("rank")

# Find the country of the user with the most followers

max_followers_value = top_poster_per_country.agg(max("followers")).collect()[0][0]

country_of_max_followers = top_poster_per_country.filter(col("followers") == max_followers_value).select("country", "followers")

display(country_of_max_followers)



country followers Anguilla 15000000

In [0]:
# Find the most popular category based on different age groups 

user_pin_df = df_user_parquet.join(df_pin_parquet, on="ind", how="inner")

df_with_age_group = user_pin_df.withColumn(
    "age_group", 
    when(col("age").between(18, 24), "18-24")
    .when(col("age").between(25, 35), "25-35")
    .when(col("age").between(35, 50), "35-50")
    .otherwise("50+")
)

age_cat_counts = df_with_age_group.groupBy("age_group", "category") \
                                .agg(count("*").alias("Count")) 

most_popular_category_per_age_group = age_cat_counts.withColumn("rank", rank().over(Window.partitionBy("age_group").orderBy(desc("Count")))).filter(col("rank") == 1).drop("rank")

display(most_popular_category_per_age_group)

age_group category Count 18-24 tattoos 615 25-35 christmas 321 35-50 vehicles 215 50+ vehicles 114

In [0]:
# Find the median follower count for different age groups

median_followers = df_with_age_group.groupBy("age_group").agg(round(avg("follower_count"), 2).alias("median_follower_count"))

median_followers = median_followers.orderBy("age_group")

display(median_followers)

age_group median_follower_count 18-24 698641.96 25-35 201852.99 35-50 82185.51 50+ 52262.83

In [0]:
# Find how many users have joined each year

df_user_parquet_with_year = df_user_parquet.withColumn("post_year", year(col("date_joined")))

users_per_year = df_user_parquet_with_year.groupBy("post_year").agg(count("*").alias("number_users_joined"))

users_per_year = users_per_year.orderBy("post_year")

display(users_per_year)

post_year number_users_joined 2015 4507 2016 4791 2017 1856

In [0]:
# Find the median follower count of users based on their joining year

user_pin_df_with_year = df_user_parquet_with_year.join(df_pin_parquet, on="ind", how="inner")

median = user_pin_df_with_year.groupBy("post_year").agg(percentile_approx("follower_count", 0.5).alias("median_follower_count"))

display(median)

post_year median_follower_count 2015 160000 2016 20000 2017 4000

In [0]:
# Find the median follower count of users based on their joining year and age group

df_with_year_age = df_with_age_group.withColumn("post_year", year(col("date_joined")))

median_year_age = df_with_year_age.groupBy("post_year", "age_group").agg(percentile_approx("follower_count", 0.5).alias("median_follower_count"))

median_year_age = median_year_age.orderBy("post_year", "age_group")
display(median_year_age)

post_year age_group median_follower_count 2015 18-24 375000 2015 25-35 37000 2015 35-50 22000 2015 50+ 11000 2016 18-24 46000 2016 25-35 24000 2016 35-50 9000 2016 50+ 3000 2017 18-24 7000 2017 25-35 4000 2017 35-50 3000 2017 50+ 3000